## 쿠다 설정

In [1]:
import torch
print(torch.__version__)  # 2.6.0

2.6.0+cu126


In [4]:
import torch
print(torch.cuda.is_available())  # GPU 사용 가능 여부
print(torch.cuda.current_device())  # GPU 장치 번호 (0이 RTX 3070)
print(torch.cuda.get_device_name(0))  # GPU 이름 (NVIDIA GeForce RTX 3070)
print(torch.version.cuda)  # CUDA 버전 (12.6)

True
0
NVIDIA GeForce RTX 3070 Ti Laptop GPU
12.6


## CycleGAN 학습

## 안해도 되는것들

In [8]:
import pandas as pd
import os
import shutil

# 경로 설정 (Windows 경로에 맞게 수정)
dataset_dir = r'C:\project3\night_change_test'  # 실제 경로로 변경
image_dir = os.path.join(dataset_dir, 'nexet_2017_1')  # 이미지 폴더 경로
metadata_file = os.path.join(dataset_dir, 'train.csv')  # 메타데이터 파일 이름 확인 후 변경 (labels.csv가 아닌 train.csv로 수정)

In [9]:
# 출력 폴더 생성
day_dir = os.path.join(dataset_dir, 'Day')
night_dir = os.path.join(dataset_dir, 'Night')
twilight_dir = os.path.join(dataset_dir, 'Twilight')

os.makedirs(day_dir, exist_ok=True)
os.makedirs(night_dir, exist_ok=True)
os.makedirs(twilight_dir, exist_ok=True)

In [10]:
# 메타데이터 파일 존재 여부 확인
if not os.path.exists(metadata_file):
    print(f"Error: Metadata file not found at {metadata_file}")
    exit()

# 메타데이터 파일 로드
try:
    metadata = pd.read_csv(metadata_file)
    print("Metadata loaded successfully!")
    print(metadata.head())  # 메타데이터의 처음 5행 출력으로 구조 확인
except Exception as e:
    print(f"Error loading metadata file: {e}")
    exit()

Metadata loaded successfully!
                                      image_filename  lighting city
0  frame_20f328fa-2459-46d0-97a5-5ae2d6103cb0_000...  Twilight  NYC
1  frame_927bde20-f97f-48c2-af30-f9127b6b32ce_000...       Day  NYC
2  frame_67012509-f3bd-4175-a9d2-565a7b6bb3c7_000...       Day  NYC
3  frame_bd043377-6fb8-407a-95e5-7deb1fbab13a_000...       Day  NYC
4  frame_4da1583b-58d0-4893-8149-54541191031d_000...       Day  NYC


In [11]:
# 각 이미지를 시간대에 따라 분리
for index, row in metadata.iterrows():
    filename = row['image_filename']  # 이미지 파일 이름 (열 이름이 다를 수 있으니 확인 필요)
    time_of_day = row['lighting']  # 시간대 (Day, Night, Twilight) (열 이름이 다를 수 있으니 확인 필요)
    
    # 이미지 파일 경로
    src_path = os.path.join(image_dir, filename)
    
    # 파일이 존재하는지 확인
    if not os.path.exists(src_path):
        print(f"Image {filename} not found, skipping...")
        continue
    
    # 시간대에 따라 적절한 폴더로 이동
    if time_of_day == 'Day':
        dst_path = os.path.join(day_dir, filename)
    elif time_of_day == 'Night':
        dst_path = os.path.join(night_dir, filename)
    elif time_of_day == 'Twilight':
        dst_path = os.path.join(twilight_dir, filename)
    else:
        print(f"Unknown time_of_day {time_of_day} for {filename}, skipping...")
        continue
    
    # 파일 복사 또는 이동
    shutil.copy(src_path, dst_path)  # 복사하려면 copy, 이동하려면 move 사용
    print(f"Moved {filename} to {time_of_day} folder")

Moved frame_20f328fa-2459-46d0-97a5-5ae2d6103cb0_00000-1280_720.jpg to Twilight folder
Moved frame_927bde20-f97f-48c2-af30-f9127b6b32ce_00000-1280_720.jpg to Day folder
Moved frame_67012509-f3bd-4175-a9d2-565a7b6bb3c7_00001-1280_720.jpg to Day folder
Moved frame_bd043377-6fb8-407a-95e5-7deb1fbab13a_00004-1280_720.jpg to Day folder
Moved frame_4da1583b-58d0-4893-8149-54541191031d_00000-1280_720.jpg to Day folder
Moved frame_0726993f-b5d9-458f-8abb-08cd48633e23_00000-1280_720.jpg to Night folder
Moved frame_5fc7aa83-5bcc-4727-9a26-2d6043888efa_00000-1280_720.jpg to Night folder
Moved frame_23f17d60-6a66-4010-af8e-aca216fb3bf8_00001-1280_720.jpg to Night folder
Moved frame_2ee2a8a2-d113-443c-a519-b34b02987ebd_00000-1280_720.jpg to Night folder
Moved frame_10ef103d-9163-4f7a-b985-366ad1fc891f_00000-1280_720.jpg to Night folder
Moved frame_87a79a61-6379-4e73-9abb-a4a4c1450ac1_00000-1280_720.jpg to Night folder
Moved frame_49d0e046-7b73-4c93-a018-bc08506a7c11_00002-1280_720.jpg to Day folder

## 데이터셋 분리

In [11]:
import os
import shutil
import random

# 경로 설정
dataset_dir = r'C:\project3\night_change_test'
day_dir = os.path.join(dataset_dir, 'Day')
night_dir = os.path.join(dataset_dir, 'Night')

# # CycleGAN 데이터셋 폴더 생성
# cyclegan_dataset_dir = os.path.join(dataset_dir, 'dataset')
# trainA_dir = os.path.join(cyclegan_dataset_dir, 'trainA') # 주간 이미지 (Day 폴더에서 복사)
# trainB_dir = os.path.join(cyclegan_dataset_dir, 'trainB') # 야간 이미지 (Night 폴더에서 복사)
# testA_dir = os.path.join(cyclegan_dataset_dir, 'testA') # 테스트용 주간 이미지 (Day 폴더에서 일부 복사)
# testB_dir = os.path.join(cyclegan_dataset_dir, 'testB') # 테스트용 야간 이미지 (Night 폴더에서 일부 복사사)

# os.makedirs(trainA_dir, exist_ok=True)
# os.makedirs(trainB_dir, exist_ok=True)
# os.makedirs(testA_dir, exist_ok=True)
# os.makedirs(testB_dir, exist_ok=True)

# # Day와 Night 폴더에서 이미지 목록 가져오기
# day_images = [f for f in os.listdir(day_dir) if f.endswith('.jpg')]
# night_images = [f for f in os.listdir(night_dir) if f.endswith('.jpg')]

# # 학습/테스트 데이터 비율 설정 (80% 학습, 20% 테스트)
# train_ratio = 0.8

# # Day 이미지 분리
# random.shuffle(day_images)
# train_day_count = int(len(day_images) * train_ratio)
# train_day_images = day_images[:train_day_count]
# test_day_images = day_images[train_day_count:]

# # Night 이미지 분리
# random.shuffle(night_images)
# train_night_count = int(len(night_images) * train_ratio)
# train_night_images = night_images[:train_night_count]
# test_night_images = night_images[train_night_count:]

# # 파일 복사
# for img in train_day_images:
#     shutil.copy(os.path.join(day_dir, img), os.path.join(trainA_dir, img))
# for img in test_day_images:
#     shutil.copy(os.path.join(day_dir, img), os.path.join(testA_dir, img))
# for img in train_night_images:
#     shutil.copy(os.path.join(night_dir, img), os.path.join(trainB_dir, img))
# for img in test_night_images:
#     shutil.copy(os.path.join(night_dir, img), os.path.join(testB_dir, img))

# print(f"Copied {len(train_day_images)} Day images to trainA")
# print(f"Copied {len(test_day_images)} Day images to testA")
# print(f"Copied {len(train_night_images)} Night images to trainB")
# print(f"Copied {len(test_night_images)} Night images to testB")

## 실제로 돌려야하는것들 (CycleGAN 학습파트)

In [2]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Dataset
from torchvision import transforms
from PIL import Image
import os
import itertools

In [3]:
# 1. 데이터셋 클래스 정의
class ImageDataset(Dataset):
    def __init__(self, root_A, root_B, transform=None):
        self.transform = transform
        self.files_A = sorted([os.path.join(root_A, f) for f in os.listdir(root_A) if f.endswith('.jpg')])
        self.files_B = sorted([os.path.join(root_B, f) for f in os.listdir(root_B) if f.endswith('.jpg')])

    def __len__(self):
        return min(len(self.files_A), len(self.files_B))

    def __getitem__(self, index):
        img_A = Image.open(self.files_A[index % len(self.files_A)]).convert('RGB')
        img_B = Image.open(self.files_B[index % len(self.files_B)]).convert('RGB')

        if self.transform:
            img_A = self.transform(img_A)
            img_B = self.transform(img_B)

        return {'A': img_A, 'B': img_B}

In [4]:
# 2. 생성자 (Generator) 정의
class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()
        self.model = nn.Sequential(
            nn.Conv2d(3, 64, 4, stride=2, padding=1),
            nn.ReLU(inplace=True),
            nn.Conv2d(64, 128, 4, stride=2, padding=1),
            nn.InstanceNorm2d(128),
            nn.ReLU(inplace=True),
            nn.Conv2d(128, 256, 4, stride=2, padding=1),
            nn.InstanceNorm2d(256),
            nn.ReLU(inplace=True),
            nn.ConvTranspose2d(256, 128, 4, stride=2, padding=1),
            nn.InstanceNorm2d(128),
            nn.ReLU(inplace=True),
            nn.ConvTranspose2d(128, 64, 4, stride=2, padding=1),
            nn.InstanceNorm2d(64),
            nn.ReLU(inplace=True),
            nn.ConvTranspose2d(64, 3, 4, stride=2, padding=1),
            nn.Tanh()
        )

    def forward(self, x):
        return self.model(x)

In [5]:
class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()
        self.model = nn.Sequential(
            nn.Conv2d(3, 64, 4, stride=2, padding=1),    # 256x256 → 128x128
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(64, 128, 4, stride=2, padding=1),   # 128x128 → 64x64
            nn.InstanceNorm2d(128),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(128, 256, 4, stride=2, padding=1),  # 64x64 → 32x32
            nn.InstanceNorm2d(256),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(256, 512, 4, stride=2, padding=1),  # 32x32 → 16x16
            nn.InstanceNorm2d(512),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Conv2d(512, 1, 4, stride=1, padding=1)     # 16x16 → 16x16
        )

    def forward(self, x):
        return self.model(x)

In [6]:
# 4. 학습 설정
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda')

In [21]:
# 데이터 전처리
transform = transforms.Compose([
    transforms.Resize((512, 512)),
    transforms.ToTensor(),
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
])

In [12]:
# 데이터셋 로드
dataset = ImageDataset(
    root_A=os.path.join(dataset_dir, 'dataset/trainA'),
    root_B=os.path.join(dataset_dir, 'dataset/trainB'),
    transform=transform
)
dataloader = DataLoader(dataset, batch_size=4, shuffle=True)

In [13]:
# 모델 초기화
G = Generator().to(device)  # 주간 → 야간
F = Generator().to(device)  # 야간 → 주간
D_A = Discriminator().to(device)  # 주간 판별자
D_B = Discriminator().to(device)  # 야간 판별자

In [14]:
# 손실 함수
criterion_GAN = nn.MSELoss()
criterion_cycle = nn.L1Loss()
criterion_identity = nn.L1Loss()

In [23]:
# 옵티마이저
optimizer_G = optim.Adam(itertools.chain(G.parameters(), F.parameters()), lr=0.0002, betas=(0.5, 0.999))
optimizer_D_A = optim.Adam(D_A.parameters(), lr=0.0002, betas=(0.5, 0.999))
optimizer_D_B = optim.Adam(D_B.parameters(), lr=0.0002, betas=(0.5, 0.999))

# 5. 학습 루프
num_epochs = 500 # 에포크 수는 데이터 크기에 따라 조정
lambda_cycle = 10.0
lambda_identity = 5.0

In [ ]:
for epoch in range(num_epochs):
    for i, batch in enumerate(dataloader):
        real_A = batch['A'].to(device)
        real_B = batch['B'].to(device)

        # 생성자 학습
        optimizer_G.zero_grad()

        # Identity loss
        same_B = G(real_B)
        loss_identity_B = criterion_identity(same_B, real_B) * lambda_identity
        same_A = F(real_A)
        loss_identity_A = criterion_identity(same_A, real_A) * lambda_identity

        # GAN loss
        fake_B = G(real_A)
        pred_fake = D_B(fake_B)
        real_label = torch.ones_like(pred_fake).to(device)  # 동적 크기 조정
        fake_label = torch.zeros_like(pred_fake).to(device)  # 동적 크기 조정
        loss_GAN_G = criterion_GAN(pred_fake, real_label)

        fake_A = F(real_B)
        pred_fake = D_A(fake_A)
        real_label = torch.ones_like(pred_fake).to(device)  # 동적 크기 조정
        fake_label = torch.zeros_like(pred_fake).to(device)  # 동적 크기 조정
        loss_GAN_F = criterion_GAN(pred_fake, real_label)

        # Cycle loss
        recovered_A = F(fake_B)
        loss_cycle_A = criterion_cycle(recovered_A, real_A) * lambda_cycle
        recovered_B = G(fake_A)
        loss_cycle_B = criterion_cycle(recovered_B, real_B) * lambda_cycle

        # Total loss
        loss_G = loss_GAN_G + loss_GAN_F + loss_cycle_A + loss_cycle_B + loss_identity_A + loss_identity_B
        loss_G.backward()
        optimizer_G.step()

        # 판별자 A 학습
        optimizer_D_A.zero_grad()
        pred_real = D_A(real_A)
        real_label = torch.ones_like(pred_real).to(device)  # 동적 크기 조정
        loss_D_real = criterion_GAN(pred_real, real_label)
        pred_fake = D_A(fake_A.detach())
        fake_label = torch.zeros_like(pred_fake).to(device)  # 동적 크기 조정
        loss_D_fake = criterion_GAN(pred_fake, fake_label)
        loss_D_A = (loss_D_real + loss_D_fake) * 0.5
        loss_D_A.backward()
        optimizer_D_A.step()

        # 판별자 B 학습
        optimizer_D_B.zero_grad()
        pred_real = D_B(real_B)
        real_label = torch.ones_like(pred_real).to(device)  # 동적 크기 조정
        loss_D_real = criterion_GAN(pred_real, real_label)
        pred_fake = D_B(fake_B.detach())
        fake_label = torch.zeros_like(pred_fake).to(device)  # 동적 크기 조정
        loss_D_fake = criterion_GAN(pred_fake, fake_label)
        loss_D_B = (loss_D_real + loss_D_fake) * 0.5
        loss_D_B.backward()
        optimizer_D_B.step()

        if i % 100 == 0:
            print(f'Epoch [{epoch}/{num_epochs}] Batch [{i}/{len(dataloader)}] '
                  f'Loss_G: {loss_G.item():.4f} Loss_D_A: {loss_D_A.item():.4f} Loss_D_B: {loss_D_B.item():.4f}')

    # 모델 저장
    torch.save(G.state_dict(), os.path.join(dataset_dir, f'generator_G_epoch_{epoch}.pth'))
    torch.save(F.state_dict(), os.path.join(dataset_dir, f'generator_F_epoch_{epoch}.pth'))

Epoch [0/500] Batch [0/140] Loss_G: 3.3974 Loss_D_A: 0.0041 Loss_D_B: 0.0004
Epoch [0/500] Batch [100/140] Loss_G: 3.9328 Loss_D_A: 0.0018 Loss_D_B: 0.0404
Epoch [1/500] Batch [0/140] Loss_G: 3.9986 Loss_D_A: 0.0028 Loss_D_B: 0.0155
Epoch [1/500] Batch [100/140] Loss_G: 3.5179 Loss_D_A: 0.1129 Loss_D_B: 0.0428
Epoch [2/500] Batch [0/140] Loss_G: 3.8971 Loss_D_A: 0.0040 Loss_D_B: 0.0127
Epoch [2/500] Batch [100/140] Loss_G: 3.6095 Loss_D_A: 0.0052 Loss_D_B: 0.0055
Epoch [3/500] Batch [0/140] Loss_G: 3.3770 Loss_D_A: 0.0020 Loss_D_B: 0.0048
Epoch [3/500] Batch [100/140] Loss_G: 3.9085 Loss_D_A: 0.0051 Loss_D_B: 0.0014
Epoch [4/500] Batch [0/140] Loss_G: 3.5303 Loss_D_A: 0.0020 Loss_D_B: 0.0023
Epoch [4/500] Batch [100/140] Loss_G: 3.4158 Loss_D_A: 0.0015 Loss_D_B: 0.0012
Epoch [5/500] Batch [0/140] Loss_G: 3.3252 Loss_D_A: 0.0070 Loss_D_B: 0.0010
Epoch [5/500] Batch [100/140] Loss_G: 3.1610 Loss_D_A: 0.1762 Loss_D_B: 0.0085
Epoch [6/500] Batch [0/140] Loss_G: 3.0589 Loss_D_A: 0.1640 Loss

## 밤 사진으로 바꾸는 코드

In [ ]:
import torch
import torch.nn as nn
from torchvision import transforms
from PIL import Image
import os

# 1. Generator 클래스 정의 (학습 코드에서 재사용)
class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()
        self.model = nn.Sequential(
            nn.Conv2d(3, 64, 4, stride=2, padding=1),
            nn.ReLU(inplace=True),
            nn.Conv2d(64, 128, 4, stride=2, padding=1),
            nn.InstanceNorm2d(128),
            nn.ReLU(inplace=True),
            nn.Conv2d(128, 256, 4, stride=2, padding=1),
            nn.InstanceNorm2d(256),
            nn.ReLU(inplace=True),
            nn.ConvTranspose2d(256, 128, 4, stride=2, padding=1),
            nn.InstanceNorm2d(128),
            nn.ReLU(inplace=True),
            nn.ConvTranspose2d(128, 64, 4, stride=2, padding=1),
            nn.InstanceNorm2d(64),
            nn.ReLU(inplace=True),
            nn.ConvTranspose2d(64, 3, 4, stride=2, padding=1),
            nn.Tanh()
        )

    def forward(self, x):
        return self.model(x)

# 2. 디바이스 설정
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

# 3. 모델 초기화 및 가중치 로드
G = Generator().to(device)
dataset_dir = r'C:\Users\acorn\OneDrive\Desktop\MyWork\Battlefield-object-recognition-learning-model\night_change_test'  # 학습 시 사용한 경로
checkpoint_path = os.path.join(dataset_dir, '야간으로 바꾸는 가중치\generator_G_epoch_49.pth')  # 가장 최근 에포크 가중치
G.load_state_dict(torch.load(checkpoint_path, map_location=device))
G.eval()  # 평가 모드로 전환

# 4. 이미지 전처리 (학습 시 사용한 동일한 전처리)
transform = transforms.Compose([
    transforms.Resize((1024, 1024)),
    transforms.ToTensor(),
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
])

# 5. 입력 이미지 로드
input_image_path = r'C:\Users\acorn\OneDrive\Desktop\MyWork\Battlefield-object-recognition-learning-model\night_change_test\night_test_pic1.jpg'  # 사용자의 주간 사진 경로
input_image = Image.open(input_image_path).convert('RGB')
input_tensor = transform(input_image).unsqueeze(0).to(device)  # (1, 3, 256, 256) 형태로 변환

# 6. 야간 이미지 생성
with torch.no_grad():
    fake_night = G(input_tensor)  # 주간 → 야간 변환

# 7. 결과 이미지 저장
# 정규화 해제: [-1, 1] → [0, 1]
fake_night = fake_night * 0.5 + 0.5
# 텐서를 PIL 이미지로 변환
fake_night_image = transforms.ToPILImage()(fake_night.squeeze(0).cpu())
# 저장
output_image_path = os.path.join(dataset_dir, 'my_night_photo.jpg')
fake_night_image.save(output_image_path)
print(f"Generated night image saved at: {output_image_path}")

# 8. 결과 이미지 보기 (선택 사항)
fake_night_image.show()

<>:40: SyntaxWarning: invalid escape sequence '\g'
<>:40: SyntaxWarning: invalid escape sequence '\g'
C:\Users\acorn\AppData\Local\Temp\ipykernel_19288\1925394670.py:40: SyntaxWarning: invalid escape sequence '\g'
  checkpoint_path = os.path.join(dataset_dir, '야간으로 바꾸는 가중치\generator_G_epoch_49.pth')  # 가장 최근 에포크 가중치


Using device: cpu
Generated night image saved at: C:\Users\acorn\OneDrive\Desktop\MyWork\Battlefield-object-recognition-learning-model\night_change_test\my_night_photo2.jpg
